In [2]:
from keras.models  import load_model
import keras.backend as K

import cPickle
import sys
sys.path.insert(0, '../../preprocess')
import vectorizer

import pandas as pd
import numpy as np

from support import norm, Element_wise_weighting
aspects = ['bit', 'domain']

Using TensorFlow backend.


[]


In [3]:
vec = cPickle.load(open('../../yelpdata/total_vec_120K_embed.p', 'rb'))

In [19]:
import pandas as pd
df = pd.read_csv('../../yelpdata/total_data_120K.csv')

In [33]:
ds = df
from sklearn.model_selection import train_test_split
ds['bit'] = ds['stars'].apply(lambda x : x > 3.0)
sample, sample_2 = train_test_split(ds.index, stratify=ds[['bit', 'domain']], train_size=0.01)

In [32]:
len(samples), len(sample_2)

(1270, 125818)

In [4]:
X = vec.X

In [5]:
model = load_model('../store/weights/food/WedNov816:36:412017/loss.h5', 
                   custom_objects={'contrastive_loss' : lambda a,b:b, 
                                  'Element_wise_weighting' : Element_wise_weighting(4)})

In [6]:
model_c1 = {}
for aspect in aspects :
    model_c1[aspect] = K.function(model.get_layer('pred_'+aspect).get_layer('pool_'+aspect).inputs, 
                          [model.get_layer('pred_'+aspect).get_layer('pool_'+aspect).layers[2].output])

In [34]:
filters_pico = {}
#sample_length = 1000
#sample = np.random.choice(X.shape[0], sample_length, replace=False)
for aspect in aspects :
    filters_pico[aspect] = model_c1[aspect]([X[sample]])[0]

In [35]:
nb_act = {k:(v > 0).sum()/sample_length for k,v in filters_pico.items()}
for key in sorted(nb_act.keys()) :
    print key,nb_act[key]

bit 9
domain 24


In [36]:
activated_words = {}
for aspect in aspects :
    filters = filters_pico[aspect]
    word_activations = np.zeros((vec.vocab_size, filters.shape[2]))
    for i in range(filters.shape[2]) :
        filter_i = filters[:,:,i]
        word2filter = np.dstack((X[sample], filter_i))
        filter_w2f = word2filter[word2filter[:,:,1] > 0.0]
        for word in filter_w2f :
            word_activations[int(word[0]), i] = word[1]
    activated_words[aspect] = word_activations

In [37]:
top_words_df = pd.DataFrame()
top_words_size = 40
for aspect in aspects :
    popwords = activated_words[aspect].sum(axis=1)
    sorted_idx = np.argsort(popwords)
    top_words = sorted_idx[-top_words_size:]
    top_words = pd.Series([v for k, v in vec.idx2word.items() if k in top_words])
    top_words_df[aspect] = top_words
top_words_df

bit        domain
0          amelie           akl
1         apology       astoria
2           awful         aveda
3       behaviour          beds
4           dirty      biltmore
5      disgusting          cana
6   disinterested  conquistador
7          divine       d'orsay
8           filed     donatello
9          filthy      fairmont
10     flavorless     grandview
11         frayed     greenwich
12         hooked        harrah
13    inattentive      homewood
14      location-         hotel
15         mouldy        hotel-
16         pissed       kapalua
17     pleasantly       kimpton
18          prado         macys
19         refund      mattress
20        refused        murano
21            rer         musee
22         ripoff     organised
23           rude       penalty
24         rudely         prado
25         rusted       prepaid
26       shouting         quail
27       shrugged      radisson
28        slowest       records
29       spotless    relaxation
30       superbly       resorts
31       terrible           riu
32           ubud         rooms
33   unacceptable    snorkeling
34   unappetizing         suite
35  unpretentious    timeshares
36          urine    trastevere
37      violation          ubud
38           vons      upgrades
39          worst       yucatan

In [38]:
summed = {}
for aspect in aspects :
    summed[aspect] = filters_pico[aspect].sum(axis=-1)

In [39]:
X_words = map(lambda s : [vec.idx2word[w] for w in s], X[sample])

In [40]:
zipped = zip(X_words, summed['bit'], summed['domain'])
total_vals = []
for x,a0,a1 in zipped :
    total_vals.append(zip(x,a0,a1))
    
for abst in total_vals :
    for sent in abst :
         if sent[0] != '[0]' :
            if sent[1] > 0 and sent[2] > 0 :
                print "\033[1;33;48m "+sent[0],
            elif sent[1] > 0 :
                print "\033[1;31;48m "+sent[0], #r app
            elif sent[2] > 0 :
                print "\033[1;32;48m "+sent[0], #g aro
            else :
                print "\033[0;30;48m "+sent[0],
        
    print ''

 so  i  could  n't  really  eat  anything  at  this  place  .  i  let  the  lady  know  that  i  would  just  be  sitting  with  my  friend  .  she  then  told  me  that  she  was  going  to  charge  me  to  sit  there  .  i  asked  if  i  had  to  pay  even  though  i  was  n't  eating  and  she  said  yes  .  such  a  stupid  thing  .  i  just  said  fuck  it  because  i  'm  not  going  pay  to  sit  there  to  watch  people  eat  .  what  a  terrible  experience  .  they  should  have  a  disclaimer  on  their  sign  that  says  "  you  have  to  pay  even  if  you  ca  n't  eat  anything  here  .  "  i  'll  be  sure  to  never  go  to  this  place  again  .  it  was  beautiful  inside  but  the  lady  taking  orders  was  a  complete  bitch  . 
 i  love  tropical  smoothie  .  sadly  ,  this  one  disappoints  .  my  friend  and  i  left  after  not  even  being  acknowledged  by  the  employees  after  qqq  minutes  of  waiting  .  bad  customer  service  and  long  wait  time  

 we  travelled  here  as  part  of  our  honeymoon  ,  coming  from  staying  qqq  nights  at  the  unk  -  la  in  kowloon  (  hong  kong  )  .  the  singapore  shangri  -  la  was  just  as  fantastic  as  the  kowloon  hotel  .  service  amazing  .  staff  so  helpful  .  loads  of  free  gifts  for  honeymooners  .  ideal  location  .  huge  room  .  we  were  upgraded  to  a  deluxe  room  in  the  garden  wing  -  well  worth  it  -  views  over  the  swimming  pool  .  the  food  was  fantastic  -  had  room  service  dinner  as  we  were  on  honeymoon  !  what  i  loved  most  were  the  door  men  dressed  up  in  their  unk  !  highly  recommended  . 
 my  husband  and  i  were  told  of  ellis  island  by  my  co  worker  .     we  went  out  to  dinner  there  on  our  first  night  in  vegas  and  took  my  uncle  .     we  have  found  a  new  place  we  will  stop  every  time  we  go  to  vegas  .     my  uncle  loved  it  and  he  is  picky  !     my  husband  had  th

 i  loved  this  place  !  the  decor  was  fabulous  and  the  lady  that  served  me  was  a  sweetheart  .  i  ordered  the  cuban  and  a  cafe  mocha  and  while  it  did  take  quite  some  time  (  considering  i  was  the  only  person  in  the  place  )  to  get  both  my  drink  and  my  food  ,  i  was  still  overly  impressed  .  my  sandwich  was  so  good  ,  and  even  the  fries  were  good  .  they  tasted  just  like  the  food  i  had  while  i  visited  cuba  a  couple  years  ago  .  i  will  definitely  be  coming  back  here  since  i  live  within  walking  distance  . 
 artisan  pizza  .  delicious  .  fresh  ingredients  .     creative  recipes  .     when  the  chef  pulled  out  the  fresh  basil  ,  we  could  smell  it  qqq  feet  away  .  we  had  their  pizza  at  the  unk  in  unk  ,  and  were  quite  impressed  .     it  's  a  food  trailer  with  killer  pizza  !  highly  recommended  .  the  staff  is  knowledgeable  and  enthusiastic  .  

 other

 we  decided  we  would  go  to  berlin  for  new  year  and  was  pleasantly  surprised  that  we  could  get  a  hotel  at  a  reasonable  price  that  looked  quite  stylish  .  unk  the  hotel  looks  fine  and  has  been  dressed  very  simply  .  in  terms  of  location  ,  there  are  a  number  of  nice  bars  and  restaurants  within  qqq  minutes  walk  and  the  excellent  trains  are  also  easily  accessible  within  qqq  minutes  .  the  journey  from  the  airport  was  approximately  qqq  minutes  from  unk  .  breakfast  was  n't  included  but  i  believe  you  could  purchase  a  few  things  from  behind  the  very  small  bar  but  we  found  a  decent  coffee  shop  along  the  road  .  the  bar  itself  unk  into  the  reception  area  and  was  very  sparse  in  terms  of  furniture  ;  i  do  n't  think  it  would  take  very  long  for  all  seating  to  be  taken  .  generally  it  was  quite  a  cold  atmosphere  in  the  hotel  and  did  n't  feel  that  we

 confirm  your  reservation  !  !  !  !  booked  a  sat  night  in  january  on  the  web  site  .  when  i  checked  in  august  qqq  th  we  were  told  that  the  rooms  were  sold  out  .  they  offered  us  a  lower  priced  room  but  this  was  not  what  we  unk  was  a  club  level  .  overall  the  hotel  is  clean  .  front  desk  staff  could  not  care  less  about  us  until  we  spoke  to  a  manager  who  gave  us  money  off  the  room  .  i  would  hesitate  booking  this  chain  since  they  unk  rooms  . 
 to  the  host  joe  .  he  informed  me  that  i  could  n't  get  qqq  for  qqq  tickets  ,  but  that  i  could  have  $  qqq  off  each  ticket  and  he  could  give  us  comp  .  tickets  for  the  todd  paul  show  at  qqq  pm  .  so  we  agreed  ,  hoping  to  just  enjoy  a  nice  meal  at  the  unk  's  unk  and  then  make  it  to  the  todd  paul  show  and  then  the  purple  unk  show  .  well  we  go  up  to  the  qqq  pm  show  and  other  people  wh

...

 prior  to  our  trip  i  followed  the  paramount  hotel  on  facebook  and  told  them  that  we  were  looking  forward  to  staying  with  them  and  that  we  were  going  to  be  getting  married  next  year  and  that  our  trip  was  to  sort  some  wedding  stuff  out  .  we  found  the  hotel  very  easily  on  arrival  and  it  is  literally  a  stone  's  throw  from  times  square  .  on  entering  the  hotel  the  lobby  is  unk  decorated  with  comfortable  eclectic  chairs  and  sofa  's  and  soft  lighting  .  on  checking  in  we  met  the  most  helpful  and  friendly  member  's  of  staff  who  on  checking  my  details  unk  me  and  my  fiancee  on  our  unk  wedding  -  they  had  obviously  made  a  note  from  my  comment  on  facebook  .  as  a  mini  present  to  us  we  were  advised  that  the  hotel  had  given  us  a  complimentary  room  upgrade  to  a  king  size  room  !  i  was  very  impressed  by  this  little  gesture  .  the  room  was  very  c

 from  check  in  to  check  out  at  the  wynn  was  the  best  experience  my  unk  and  i  have  ever  had  on  a  vacation  .  check  in  was  fast  and  efficient  .  the  resort  room  was  immaculate  and  spotless  (  i  will  post  pictures  later  )  .  it  was  located  on  the  qqq  floor  (  on  the  unk  side  of  the  hotel  )  overlooking  the  waterfalls  .  unk  !  !  !  !  the  view  was  amazing  and  at  night  we  left  the  drapes  opened  and  unk  the  lights  and  unk  show  at  treasure  island  ,  the  mirage  ,  the  venetian  (  unk  unk  's  palace  ,  the  trump  towers  --  omg  --  just  simply  amazing  .  i  slept  like  a  baby  each  night  and  morning  -  no  construction  noise  or  unk  neighbors  .  the  encore  building  was  more  than  qqq  %  wrapped  and  the  venetian  addition  only  had  about  four  more  floors  to  wrap  .  the  bathroom  was  divine  and  sparkling  clean  with  a  big  modern  soaking  tub  ,  separate  unk  showe

 in  qqq  years  of  travelling  this  is  by  far  the  worst  hotel  i  have  stayed  in  ,  the  only  good  thing  about  it  is  its  location  ,  took  qqq  hr  to  check  in  ,  then  qqq  hrs  to  find  a  room  that  was  barely  unk  (  tried  qqq  different  rooms  )  only  reason  for  staying  was  lack  of  availability  in  unk  ,  (  arrived  qqq  december  )  some  staff  seemed  concerned  by  number  of  complaints  ,  others  uncaring  .  had  heard  bad  reports  but  upon  viewing  website  decided  to  take  a  chance  ,  big  mistake  !  !  !  definitely  not  recommended  !  !  ! 
 great  for  burger  and  brews  with  an  excellent  happy  hour  .  today  i  wanted  to  go  to  the  hash  house  but  found  out  they  were  no  longer  at  the  m  ;  i  was  told  by  one  of  the  girls  that  this  place  served  a  pretty  mean  breakfast  !  !  !  our  waitress  unk  was  lively  and  delight  !  !  !  we  hung  outside  near  poolside  and  the  food  was

 and  whatever  you  do  ...  do  n't  leave  without  having  some  "  gooey  butter  cake  "  omg  !  ! 
 this  is  an  excellent  choice  for  new  york  ,  where  even  some  of  the  chain  hotels  are  horrible  .  we  needed  to  get  my  parents  ,  they  re  almost  qqq  a  change  of  rooms  ,  the  staff  were  fine  ,  no  hassle  and  actually  relocated  them  in  the  room  next  to  us  without  being  asked  .  we  were  on  the  qqq  floor  overlooking  broadway  &  times  sq  .  as  you  come  out  of  the  hotel  you  turn  right  for  broadway  &  time  sq  ,  try  turning  left  for  stores  &  restraunts  that  are  not  touristy  and  do  nt  have  horrible  tourist  menus  ,  the  unk  restraunt  does  unk  breakfasts  and  is  very  good  value  ,  the  unk  cuban  restraunt  is  great  ,  it  looks  a  bit  exotic  from  outside  but  unk  up  the  unk  and  go  in  ,  the  staff  are  very  friendly  new  unk  and  the  food  and  salsa  music  unk  ,  were 

 this  hotel  did  not  have  my  dates  correctly  listed  on  their  reservation  system  .  thankfully  i  had  my  confirmation  as  they  were  very  rude  about  the  dates  i  needed  to  stay  .  i  was  then  directed  the  wrong  direction  to  the  wrong  tower  to  get  to  my  room  .  the  internet  service  did  not  work  ,  the  hotel  signage  is  very  poor  ,  the  restaurant  ,  unk  grill  had  the  rudest  bartender  i  have  ever  seen  .  he  ignored  me  for  quite  some  time  as  i  was  alone  and  wanting  to  order  a  drink  and  dinner  .  he  was  busy  unk  around  with  some  sort  of  problem  with  the  register  .  finally  i  asked  if  he  knew  i  was  there  and  the  reply  was  "  yeah  ,  i  have  to  fix  this  first  .  "  i  was  there  for  a  very  large  convention  that  was  held  in  the  hotel  and  on  several  occasions  had  meetings  in  the  rocks  bar  as  it  was  convenient  to  meet  for  attendees  .  on  the  qqq  occas

In [ ]:
get_ipython().system('cp "Filter Viz Single.ipynb" '+results_folder)